In [1]:
!pip install datasets --upgrade
!pip install evaluate
!pip install jiwer
!pip install accelerate -U
!pip install transformers[torch]
!pip install pytorch_lightning
!pip install hydra-core
!pip install -U 'wandb>=0.12.10'

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 kB 3.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 16.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 1.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 18.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 776.9/776.9 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 806.1/806.1 kB 14.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.5/154.5 kB 1.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.5/79.5 kB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.0/117.0 kB 11.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for antlr4-python3-runtime: filename=antlr4_

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.6/190.6 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 252.8/252.8 kB 3.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 3.8 MB/s eta 0:00:00


In [2]:
MODEL_PROCESSOR_CHECKPOINT = "openai/whisper-small"
FEATURE_TOKEN_CHECKPOINT = "openai/whisper-small"
DATASET_NAME = "bond005/sberdevices_golos_10h_crowd"

## Huggingface login


In [3]:
from huggingface_hub import notebook_login

notebook_login()

## WanDB login

In [4]:
from pytorch_lightning.loggers import WandbLogger
import wandb

wandb.login()

<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

## Load tokenizer and feature extractor

In [5]:
from transformers import WhisperFeatureExtractor, WhisperTokenizer

feature_extractor = WhisperFeatureExtractor.from_pretrained(FEATURE_TOKEN_CHECKPOINT)
tokenizer = WhisperTokenizer.from_pretrained(FEATURE_TOKEN_CHECKPOINT, language="russian", task="transcribe")

preprocessor_config.json:   0%|          | 0.00/185k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/805 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/836k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.48M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/494k [00:00<?, ?B/s]

normalizer.json:   0%|          | 0.00/52.7k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.08k [00:00<?, ?B/s]

## Load and Preprocess unprocessed Dataset and preprocess it 
(you can skip it and download already preprocessed one)

In [ ]:
from datasets import load_dataset, Audio

common_voice = load_dataset(DATASET_NAME)
common_voice = common_voice.cast_column("audio", Audio(sampling_rate=16000))

In [ ]:
def prepare_dataset(batch):
    audio = batch["audio"]

    batch["text"] = batch["transcription"] if batch["transcription"] else ""
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    batch["labels"] = tokenizer(batch["text"]).input_ids #or sentence
    return batch

In [ ]:
common_voice = common_voice.map(prepare_dataset, remove_columns=common_voice.column_names["train"], num_proc=2)

In [ ]:
common_voice

## Upload dataset

In [ ]:
common_voice.push_to_hub('gggggggg123/sber-golos')

## Load preproccessed dataset

In [8]:
from datasets import load_dataset

common_voice = load_dataset('gggggggg123/sber-golos')

Resolving data files:   0%|          | 0/20 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/20 [00:00<?, ?it/s]

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/7993 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/793 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/9994 [00:00<?, ? examples/s]

## Load Processor and Model

In [9]:
from transformers import WhisperProcessor, WhisperForConditionalGeneration

processor = WhisperProcessor.from_pretrained(MODEL_PROCESSOR_CHECKPOINT, language="russian", task="transcribe")
model = WhisperForConditionalGeneration.from_pretrained(MODEL_PROCESSOR_CHECKPOINT)

config.json:   0%|          | 0.00/1.97k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.84k [00:00<?, ?B/s]

## DataCollator, Config, and Metrics

In [10]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [11]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [12]:
import evaluate

metric = evaluate.load("wer")

In [13]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    for index in reversed(range(len(label_str))):
      if label_str[index] == '':
        del label_str[index]
        del pred_str[index]

    print("="*len(label_str))
    print(label_str)
    print(pred_str)
    print("="*len(label_str))

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [14]:
metric.compute(predictions=["п р и в е т"], references=["п р ы в е т"])

0.16666666666666666

In [15]:
model.config.forced_decoder_ids = None
model.config.suppress_tokens = []

## Training

In [16]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./whisper-small-ru-golos",  # change to a repo name of your choice
    per_device_train_batch_size=8,
    gradient_accumulation_steps=2,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=300,
    max_steps=3000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["wandb"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
    hub_strategy="all_checkpoints",
    num_train_epochs=2
)


In [17]:
from transformers import Seq2SeqTrainer
from pytorch_lightning.loggers import WandbLogger

wandb_logger = WandbLogger(log_model="all")

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=common_voice["train"],
    eval_dataset=common_voice["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)

In [18]:
trainer.train()

wandb: Currently logged in as: gosha-zorabov (slav-gosh-tg). Use `wandb login --relogin` to force relogin


/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...


['шестьдесят тысяч тенге сколько будет стоить', 'покажи мне на смотрешке телеканал синергия тв', 'заказать яблоки зеленые', 'алиса закажи килограммовый торт графские развалины', 'ищи телеканал про бизнес на тиви', 'михаила мурадяна', 'любовницы две тысячи тринадцать пятнадцатый сезон', 'найди боевики', 'гетто сезон три', 'хочу посмотреть ростов папа на телевизоре', 'сбер какое твое самое ненавистное занятие', 'афина чем платят у китайцев', 'джой как работает досрочное погашение кредита', 'у тебя найдется люк кейдж', 'у тебя будет лучшая часть пинк', 'пожалуйста пополните мне счет', 'анне павловне шабуровой', 'врубай на смотрешке муз тв', 'найди на смотрешке лдпр тв', 'сбер мне нужен педикюр забей мне место', 'галины афанасьевны', 'сколько стоимость обмена китайского юаня на российский рубль', 'обмани меня сезон восемь часть тринадцать', 'включи канал футбол эйч ди', 'поп звезда не переставай не останавливайся найти', 'салют самый популярный фильм люка бессона', 'татьяна зиганшина', 'дж

/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


['шестьдесят тысяч тенге сколько будет стоить', 'покажи мне на смотрешке телеканал синергия тв', 'заказать яблоки зеленые', 'алиса закажи килограммовый торт графские развалины', 'ищи телеканал про бизнес на тиви', 'михаила мурадяна', 'любовницы две тысячи тринадцать пятнадцатый сезон', 'найди боевики', 'гетто сезон три', 'хочу посмотреть ростов папа на телевизоре', 'сбер какое твое самое ненавистное занятие', 'афина чем платят у китайцев', 'джой как работает досрочное погашение кредита', 'у тебя найдется люк кейдж', 'у тебя будет лучшая часть пинк', 'пожалуйста пополните мне счет', 'анне павловне шабуровой', 'врубай на смотрешке муз тв', 'найди на смотрешке лдпр тв', 'сбер мне нужен педикюр забей мне место', 'галины афанасьевны', 'сколько стоимость обмена китайского юаня на российский рубль', 'обмани меня сезон восемь часть тринадцать', 'включи канал футбол эйч ди', 'поп звезда не переставай не останавливайся найти', 'салют самый популярный фильм люка бессона', 'татьяна зиганшина', 'дж

/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


['шестьдесят тысяч тенге сколько будет стоить', 'покажи мне на смотрешке телеканал синергия тв', 'заказать яблоки зеленые', 'алиса закажи килограммовый торт графские развалины', 'ищи телеканал про бизнес на тиви', 'михаила мурадяна', 'любовницы две тысячи тринадцать пятнадцатый сезон', 'найди боевики', 'гетто сезон три', 'хочу посмотреть ростов папа на телевизоре', 'сбер какое твое самое ненавистное занятие', 'афина чем платят у китайцев', 'джой как работает досрочное погашение кредита', 'у тебя найдется люк кейдж', 'у тебя будет лучшая часть пинк', 'пожалуйста пополните мне счет', 'анне павловне шабуровой', 'врубай на смотрешке муз тв', 'найди на смотрешке лдпр тв', 'сбер мне нужен педикюр забей мне место', 'галины афанасьевны', 'сколько стоимость обмена китайского юаня на российский рубль', 'обмани меня сезон восемь часть тринадцать', 'включи канал футбол эйч ди', 'поп звезда не переставай не останавливайся найти', 'салют самый популярный фильм люка бессона', 'татьяна зиганшина', 'дж

There were missing keys in the checkpoint model loaded: ['proj_out.weight'].


TrainOutput(global_step=3000, training_loss=0.12685049249231814, metrics={'train_runtime': 37145.9754, 'train_samples_per_second': 1.292, 'train_steps_per_second': 0.081, 'total_flos': 1.383997862854656e+19, 'train_loss': 0.12685049249231814, 'epoch': 6.0})

## Upload to Huggingface

In [19]:
kwargs = {
    "dataset_tags": "mbond005/sberdevices_golos_10h_crowd",
    "dataset": "sberdevices_golos_10h",  # a 'pretty' name for the training dataset
    "dataset_args": "config: ru, split: test",
    "language": "ru",
    "model_name": "Whisper Small Ru - Slava Gosha",  # a 'pretty' name for our model
    "finetuned_from": "openai/whisper-small",
    "tasks": "automatic-speech-recognition",
    "tags": "hf-asr-leaderboard",
}

In [20]:
trainer.push_to_hub(**kwargs)

'https://huggingface.co/gggggggg123/whisper-small-ru-golos/tree/main/'

## Download trained model

In [26]:
model_name = 'gggggggg123/whisper-small-ru-golos'
checkpoint_version = 'checkpoint-2000'
model = WhisperForConditionalGeneration.from_pretrained('gggggggg123/whisper-small-ru-golos')

config.json:   0%|          | 0.00/1.32k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.83k [00:00<?, ?B/s]

In [27]:
model

WhisperForConditionalGeneration(
  (model): WhisperModel(
    (encoder): WhisperEncoder(
      (conv1): Conv1d(80, 768, kernel_size=(3,), stride=(1,), padding=(1,))
      (conv2): Conv1d(768, 768, kernel_size=(3,), stride=(2,), padding=(1,))
      (embed_positions): Embedding(1500, 768)
      (layers): ModuleList(
        (0-11): 12 x WhisperEncoderLayer(
          (self_attn): WhisperAttention(
            (k_proj): Linear(in_features=768, out_features=768, bias=False)
            (v_proj): Linear(in_features=768, out_features=768, bias=True)
            (q_proj): Linear(in_features=768, out_features=768, bias=True)
            (out_proj): Linear(in_features=768, out_features=768, bias=True)
          )
          (self_attn_layer_norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
          (activation_fn): GELUActivation()
          (fc1): Linear(in_features=768, out_features=3072, bias=True)
          (fc2): Linear(in_features=3072, out_features=768, bias=True)
          (f